# Heatmap of average price per area

A geographical view of price per area in Singapore

In [1]:
import matplotlib as mpl
from matplotlib import cm
import folium
from folium.plugins import HeatMap
import pandas as pd

In [2]:
trainPath   = "train.csv"
microPath   = "properties.csv"
geoPath     = "geo_attributes.csv"

train_keys = pd.read_csv(trainPath)
micro = pd.read_csv(microPath)
geo = pd.read_csv(geoPath)

df  = pd.merge(geo, pd.merge(micro, train_keys, on = "property_key"), on = "project")
df['year'] = df['contractDate'].apply(lambda x:x[:4])
df['psm'] = df['price']/df['area']

In [3]:
base_map = folium.Map(location=[1.3521, 103.8198], control_scale=True, zoom_start=12)
fdf = df.groupby(['project']).mean(numeric_only=True).reset_index()
d = fdf[['lat', 'lng', 'psm']].values.tolist()

gradient = {.0: 'blue', .5: 'lime', 1: 'red'} # Original
m = HeatMap(d,radius=11, min_opacity=0.1, max_zoom=1, blur=12, gradient=gradient).add_to(base_map)
# FastMarkerCluster(data=fdf[['lat', 'lng']].values.tolist()).add_to(base_map)
norm = mpl.colors.Normalize(vmin=0, vmax=1)
sm = cm.ScalarMappable(norm=norm, cmap=mpl.colors.LinearSegmentedColormap.from_list('b2g', ['royalblue', 'forestgreen', 'red']))

max_psm = max(fdf['psm'])
min_psm = min(fdf['psm'])
range_psm = max_psm - min_psm
for index, row in fdf.iterrows():

    # generate the popup message that is shown on click.
    popup_text = f"PROJECT: {row['project']} <br> $psm: {row['psm']}"


    scaled_psm = (row['psm']-min_psm)/range_psm
    color = list(sm.to_rgba(scaled_psm))
    color[3] = 0.05
    folium.Circle(location=(row["lat"],
                                  row["lng"]),
                        radius=10,
                        color=mpl.colors.rgb2hex(color, keep_alpha=True),
                        popup=popup_text,
                        fill=True).add_to(base_map)

folium.LayerControl().add_to(base_map)

In [4]:
# Heatmap with labels
base_map